In [1]:
import requests
import csv

#GitHub API token
token = 'xxxxxxxxxxxxxxxxxxxxxxxxxx'

# Headers for authentication
headers = {
    'Authorization': f'token {token}'
}

# List of topics to extract data for
topics = ['machine-learning', 'data-science', 'artificial-intelligence', 'deep-learning',
          'big-data', 'data-visualization', 'natural-language-processing', 'data-engineering',
          'cloud-computing', 'data-analytics']

# Open a CSV file to save the data
with open('github_repositories_detailed.csv', 'w', newline='', encoding='utf-8') as csvfile:
    fieldnames = ['Topic', 'Repository Name', 'Owner', 'Description', 'URL', 'Programming Language', 
                  'Creation Date', 'Last Updated Date', 'Number of Stars', 'Number of Forks', 
                  'Number of Open Issues', 'License Type']
    writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
    writer.writeheader()

    total_repos = 0
    for topic in topics:
        print(f"\nFetching data for topic: {topic}")
        
        page = 1
        while total_repos < 20000:
            # URL to fetch repositories for the specific topic, sorted by stars, with pagination
            url = f'https://api.github.com/search/repositories?q=topic:{topic}&sort=stars&order=desc&per_page=100&page={page}'
            
            # Make the API request
            response = requests.get(url, headers=headers)

            # Check if the request was successful
            if response.status_code == 200:
                data = response.json()
                if not data['items']:  # If there are no more items, break the loop
                    break
                
                # Extract detailed information for each repository
                for repo in data['items']:
                    writer.writerow({
                        'Topic': topic,
                        'Repository Name': repo['name'],
                        'Owner': repo['owner']['login'],
                        'Description': repo['description'],
                        'URL': repo['html_url'],
                        'Programming Language': repo['language'],
                        'Creation Date': repo['created_at'],
                        'Last Updated Date': repo['updated_at'],
                        'Number of Stars': repo['stargazers_count'],
                        'Number of Forks': repo['forks_count'],
                        'Number of Open Issues': repo['open_issues_count'],
                        'License Type': repo['license']['name'] if repo['license'] else 'No License'
                    })
                    total_repos += 1
                    print(f"Fetched repository: {repo['name']} from {repo['owner']['login']}. Total repositories: {total_repos}")

                page += 1  # Move to the next page
            else:
                print(f"Error fetching data for topic {topic}: {response.status_code}")
                break  # Exit the loop if there's an error



Fetching data for topic: machine-learning
Fetched repository: tensorflow from tensorflow. Total repositories: 1
Fetched repository: transformers from huggingface. Total repositories: 2
Fetched repository: pytorch from pytorch. Total repositories: 3
Fetched repository: netdata from netdata. Total repositories: 4
Fetched repository: ML-For-Beginners from microsoft. Total repositories: 5
Fetched repository: cs-video-courses from Developer-Y. Total repositories: 6
Fetched repository: d2l-zh from d2l-ai. Total repositories: 7
Fetched repository: keras from keras-team. Total repositories: 8
Fetched repository: tesseract from tesseract-ocr. Total repositories: 9
Fetched repository: scikit-learn from scikit-learn. Total repositories: 10
Fetched repository: awesome-scalability from binhnguyennus. Total repositories: 11
Fetched repository: annotated_deep_learning_paper_implementations from labmlai. Total repositories: 12
Fetched repository: face_recognition from ageitgey. Total repositories: 13

Data Cleaning

In [2]:
import pandas as pd 
df = pd.read_csv("S:/DS/projects/GitHub_data_dive/github_repositories_detailed.csv")

In [3]:
df.shape

(10000, 12)

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10000 entries, 0 to 9999
Data columns (total 12 columns):
 #   Column                 Non-Null Count  Dtype 
---  ------                 --------------  ----- 
 0   Topic                  10000 non-null  object
 1   Repository Name        10000 non-null  object
 2   Owner                  10000 non-null  object
 3   Description            9881 non-null   object
 4   URL                    10000 non-null  object
 5   Programming Language   8716 non-null   object
 6   Creation Date          10000 non-null  object
 7   Last Updated Date      10000 non-null  object
 8   Number of Stars        10000 non-null  int64 
 9   Number of Forks        10000 non-null  int64 
 10  Number of Open Issues  10000 non-null  int64 
 11  License Type           10000 non-null  object
dtypes: int64(3), object(9)
memory usage: 937.6+ KB


In [5]:
df.isnull().sum()

Topic                       0
Repository Name             0
Owner                       0
Description               119
URL                         0
Programming Language     1284
Creation Date               0
Last Updated Date           0
Number of Stars             0
Number of Forks             0
Number of Open Issues       0
License Type                0
dtype: int64

In [6]:
df['Programming Language'].value_counts()

Programming Language
Python              3631
Jupyter Notebook    1732
JavaScript           501
Java                 393
C++                  327
                    ... 
NCL                    1
Smalltalk              1
Common Lisp            1
Astro                  1
Bicep                  1
Name: count, Length: 92, dtype: int64

In [7]:
# Replace "Jupyter Notebook" with "Python" ("Jupyter Notebook" is not a programme)
df['Programming Language'] = df['Programming Language'].replace('Jupyter Notebook', 'Python')

Handle missing values

In [8]:
selected_columns = df[['Programming Language', 'Description']]

# Check for null values and group by Topic
null_counts = selected_columns.isnull().groupby(df['Topic']).sum()

# Display topics with null values in Programming Language and Description
topics_with_nulls = null_counts[(null_counts['Programming Language'] > 0) | (null_counts['Description'] > 0)]
print(topics_with_nulls)


                             Programming Language  Description
Topic                                                         
artificial-intelligence                       142            1
big-data                                       71           16
cloud-computing                               192           28
data-analytics                                175           31
data-engineering                              112           23
data-science                                  119            4
data-visualization                             53            7
deep-learning                                 131            3
machine-learning                              137            3
natural-language-processing                   152            3


In [9]:
# Group by 'Topic' and calculate the mode for 'Programming Language' and 'Description'
mode_values = df.groupby('Topic').agg({
    'Programming Language': lambda x: x.mode()[0] if not x.mode().empty else None,
    'Description': lambda x: x.mode()[0] if not x.mode().empty else None
})

# Merge back the mode values to the original DataFrame
for topic, modes in mode_values.iterrows():
    df.loc[(df['Topic'] == topic) & (df['Programming Language'].isnull()), 'Programming Language'] = modes['Programming Language']
    df.loc[(df['Topic'] == topic) & (df['Description'].isnull()), 'Description'] = modes['Description']

# Check if there are still null values
print(df[['Programming Language', 'Description']].isnull().sum())


Programming Language    0
Description             0
dtype: int64


In [10]:
mode_values

Programming Language  \
Topic                                              
artificial-intelligence                   Python   
big-data                                  Python   
cloud-computing                           Python   
data-analytics                            Python   
data-engineering                          Python   
data-science                              Python   
data-visualization                        Python   
deep-learning                             Python   
machine-learning                          Python   
natural-language-processing               Python   

                                                                   Description  
Topic                                                                           
artificial-intelligence       A Configurable Recommender Systems Simulation...  
big-data                                              Mirror of Apache CouchDB  
cloud-computing              Este repositório é um acervo abrangente de tec...  
data-analytics               The primary objective of this project is to de...  
data-engineering             Apache DevLake is an open-source dev data plat...  
data-science                 Learn how to design, develop, deploy and itera...  
data-visualization                  Extra functionality for leaflet R package.  
deep-learning                Learn how to design, develop, deploy and itera...  
machine-learning             Learn how to design, develop, deploy and itera...  
natural-language-processing  A paper list for aspect based sentiment analysis.

In [11]:
df['Programming Language'].value_counts()

Programming Language
Python         6647
JavaScript      501
Java            393
C++             327
TypeScript      292
               ... 
NCL               1
Smalltalk         1
Common Lisp       1
Astro             1
Bicep             1
Name: count, Length: 91, dtype: int64

In [12]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10000 entries, 0 to 9999
Data columns (total 12 columns):
 #   Column                 Non-Null Count  Dtype 
---  ------                 --------------  ----- 
 0   Topic                  10000 non-null  object
 1   Repository Name        10000 non-null  object
 2   Owner                  10000 non-null  object
 3   Description            10000 non-null  object
 4   URL                    10000 non-null  object
 5   Programming Language   10000 non-null  object
 6   Creation Date          10000 non-null  object
 7   Last Updated Date      10000 non-null  object
 8   Number of Stars        10000 non-null  int64 
 9   Number of Forks        10000 non-null  int64 
 10  Number of Open Issues  10000 non-null  int64 
 11  License Type           10000 non-null  object
dtypes: int64(3), object(9)
memory usage: 937.6+ KB


In [13]:
# Convert Creation_Date and Last_Updated_Date
df['Creation Date'] = pd.to_datetime(df['Creation Date']).dt.strftime('%Y-%m-%d %H:%M:%S')
df['Last Updated Date'] = pd.to_datetime(df['Last Updated Date']).dt.strftime('%Y-%m-%d %H:%M:%S')

In [14]:
df.head()

Topic   Repository Name        Owner  \
0  machine-learning        tensorflow   tensorflow   
1  machine-learning      transformers  huggingface   
2  machine-learning           pytorch      pytorch   
3  machine-learning           netdata      netdata   
4  machine-learning  ML-For-Beginners    microsoft   

                                         Description  \
0  An Open Source Machine Learning Framework for ...   
1  🤗 Transformers: State-of-the-art Machine Learn...   
2  Tensors and Dynamic neural networks in Python ...   
3  Architected for speed. Automated for easy. Mon...   
4  12 weeks, 26 lessons, 52 quizzes, classic Mach...   

                                             URL Programming Language  \
0       https://github.com/tensorflow/tensorflow                  C++   
1    https://github.com/huggingface/transformers               Python   
2             https://github.com/pytorch/pytorch               Python   
3             https://github.com/netdata/netdata                    C   
4  https://github.com/microsoft/ML-For-Beginners                 HTML   

         Creation Date    Last Updated Date  Number of Stars  Number of Forks  \
0  2015-11-07 01:19:20  2024-10-09 12:44:15           185882            74241   
1  2018-10-29 13:56:00  2024-10-09 12:03:02           133112            26572   
2  2016-08-13 05:26:41  2024-10-09 11:38:05            82782            22307   
3  2013-06-17 18:39:10  2024-10-09 11:34:37            71382             5893   
4  2021-03-03 01:34:05  2024-10-09 12:36:47            69370            14354   

   Number of Open Issues                     License Type  
0                   5147               Apache License 2.0  
1                   1417               Apache License 2.0  
2                  15064                            Other  
3                    210  GNU General Public License v3.0  
4                      9                      MIT License

Data Storage

In [15]:
import mysql.connector

# Establishing the connection
mydb = mysql.connector.connect(
    host="localhost",
    user="root",
    password="xxxx",
    database='github'
)

mycursor = mydb.cursor(buffered=True)


In [16]:
table = '''
CREATE TABLE repository (
    id INT AUTO_INCREMENT PRIMARY KEY,
    topic VARCHAR(255),
    repository_name VARCHAR(255),
    owner VARCHAR(255),
    description TEXT,
    url VARCHAR(255),
    programming_language VARCHAR(100),
    creation_date DATETIME,
    last_updated_date DATETIME,
    number_of_stars INT,
    number_of_forks INT,
    number_of_open_issues INT,
    license_type VARCHAR(100)
)'''

mycursor.execute(table)
mydb.commit()

In [17]:
insert_query = """
INSERT INTO repository (
    topic, repository_Name, owner, description, url, 
    programming_language, creation_date, last_updated_date, 
    number_of_stars, number_of_forks, number_of_open_issues, 
    license_type
) VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s)
"""

for index, row in df.iterrows():
    mycursor.execute(insert_query, (
        row['Topic'], 
        row['Repository Name'], 
        row['Owner'], 
        row['Description'], 
        row['URL'], 
        row['Programming Language'], 
        row['Creation Date'], 
        row['Last Updated Date'], 
        row['Number of Stars'], 
        row['Number of Forks'], 
        row['Number of Open Issues'], 
        row['License Type']
    ))

mydb.commit()


In [18]:
mycursor.execute("SELECT * FROM repository")
results = mycursor.fetchall()
for row in results:
    print(row)


(1, 'machine-learning', 'tensorflow', 'tensorflow', 'An Open Source Machine Learning Framework for Everyone', 'https://github.com/tensorflow/tensorflow', 'C++', datetime.datetime(2015, 11, 7, 1, 19, 20), datetime.datetime(2024, 10, 9, 12, 44, 15), 185882, 74241, 5147, 'Apache License 2.0')
(2, 'machine-learning', 'transformers', 'huggingface', '🤗 Transformers: State-of-the-art Machine Learning for Pytorch, TensorFlow, and JAX.', 'https://github.com/huggingface/transformers', 'Python', datetime.datetime(2018, 10, 29, 13, 56), datetime.datetime(2024, 10, 9, 12, 3, 2), 133112, 26572, 1417, 'Apache License 2.0')
(3, 'machine-learning', 'pytorch', 'pytorch', 'Tensors and Dynamic neural networks in Python with strong GPU acceleration', 'https://github.com/pytorch/pytorch', 'Python', datetime.datetime(2016, 8, 13, 5, 26, 41), datetime.datetime(2024, 10, 9, 11, 38, 5), 82782, 22307, 15064, 'Other')
(4, 'machine-learning', 'netdata', 'netdata', 'Architected for speed. Automated for easy. Monito